I have a stituation for daily increments and my target table is huge with 1.5tb data

now while i want to perform daily increments using spark i have always truncate the total target table and perform SCD merge for whole table 

i happen to notice there could be easy solution. i have only 7 years worth of data coming into bank table. i will while writing while write data in partitioned manner which is for 20 yearas intially and then from daily incremental data i will take data and only modify related dates for past years using paritioning technique in hive and 

i want. to you to create sample data ( very short table for 20 years you can create 20 records or more if needed ) and input has 7 years updated data from current date and 
modify them using spark hive table paritionign and iwant recreate this using jupyter notebook in local folder and give me all code samples to achieve this

In [1]:
import os

# Set SPARK_HOME and JAVA_HOME environment variables
os.environ['SPARK_HOME'] = '/usr/local/Cellar/apache-spark/3.5.1/libexec'
os.environ['JAVA_HOME'] = '/usr/local/opt/openjdk/libexec/openjdk.jdk/Contents/Home'

In [2]:
from pyspark.sql import SparkSession

# Initialize SparkSession with Hive support
spark = SparkSession.builder \
    .appName("HivePartitioningExample") \
    .config("spark.sql.warehouse.dir", "/user/hive/warehouse") \
    .enableHiveSupport() \
    .getOrCreate()

spark.conf.set("spark.sql.hive.metastore.jars", "path/to/hive-metastore-jar")
spark.conf.set("spark.sql.hive.metastore.version", "3.1.2")  # Use the version of your Hive metastore

Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
24/07/31 11:23:19 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
24/07/31 11:23:20 WARN Utils: Service 'SparkUI' could not bind on port 4040. Attempting port 4041.


In [3]:
import pandas as pd
from datetime import datetime, timedelta

# Function to create sample data
def create_sample_data(start_year, end_year, num_records):
    data = []
    for year in range(start_year, end_year + 1):
        for i in range(num_records):
            date = datetime(year, 1, 1) + timedelta(days=i % 365)
            data.append((i, f"Name_{i}", date, f"Status_{i % 3}"))
    return pd.DataFrame(data, columns=["ID", "Name", "Date", "Status"])

# Create DataFrame with 20 years of data
df = create_sample_data(2004, 2023, 1000)

# Save the DataFrame to a CSV file
df.to_csv("Pyspark_learning/Issues-learning /Hive_partitioned_table_bank/sample_data.csv", index=False)


In [4]:
# Load the sample data into Spark DataFrame
df = spark.read.csv('Pyspark_learning/Issues-learning /Hive_partitioned_table_bank/sample_data.csv', header=True, inferSchema=True)

# Add a year column for partitioning
from pyspark.sql.functions import year

df = df.withColumn('year', year(df['date']))

# Show the DataFrame
df.show()

24/07/31 11:23:31 WARN GarbageCollectionMetrics: To enable non-built-in garbage collector(s) List(G1 Concurrent GC), users should configure it(them) to spark.eventLog.gcMetrics.youngGenerationGarbageCollectors or spark.eventLog.gcMetrics.oldGenerationGarbageCollectors


+---+-------+----------+--------+----+
| ID|   Name|      Date|  Status|year|
+---+-------+----------+--------+----+
|  0| Name_0|2004-01-01|Status_0|2004|
|  1| Name_1|2004-01-02|Status_1|2004|
|  2| Name_2|2004-01-03|Status_2|2004|
|  3| Name_3|2004-01-04|Status_0|2004|
|  4| Name_4|2004-01-05|Status_1|2004|
|  5| Name_5|2004-01-06|Status_2|2004|
|  6| Name_6|2004-01-07|Status_0|2004|
|  7| Name_7|2004-01-08|Status_1|2004|
|  8| Name_8|2004-01-09|Status_2|2004|
|  9| Name_9|2004-01-10|Status_0|2004|
| 10|Name_10|2004-01-11|Status_1|2004|
| 11|Name_11|2004-01-12|Status_2|2004|
| 12|Name_12|2004-01-13|Status_0|2004|
| 13|Name_13|2004-01-14|Status_1|2004|
| 14|Name_14|2004-01-15|Status_2|2004|
| 15|Name_15|2004-01-16|Status_0|2004|
| 16|Name_16|2004-01-17|Status_1|2004|
| 17|Name_17|2004-01-18|Status_2|2004|
| 18|Name_18|2004-01-19|Status_0|2004|
| 19|Name_19|2004-01-20|Status_1|2004|
+---+-------+----------+--------+----+
only showing top 20 rows



In [5]:
# Drop the table if it exists
spark.sql("DROP TABLE IF EXISTS bank_table")

# Write DataFrame to Hive table with partitioning
df.write \
    .mode('overwrite') \
    .partitionBy('year') \
    .format('hive') \
    .saveAsTable('bank_table')

# Verify table creation
spark.sql("SHOW TABLES").show()
spark.sql("DESCRIBE bank_table").show()

24/07/31 11:23:48 WARN HiveConf: HiveConf of name hive.stats.jdbc.timeout does not exist
24/07/31 11:23:48 WARN HiveConf: HiveConf of name hive.stats.retries.wait does not exist
24/07/31 11:23:49 ERROR Schema: Failed initialising database.
Unable to open a test connection to the given database. JDBC url = jdbc:derby:;databaseName=metastore_db;create=true, username = APP. Terminating connection pool (set lazyInit to true if you expect to start your database after your app). Original Exception: ------
java.sql.SQLException: Failed to create database 'metastore_db', see the next exception for details.
	at org.apache.derby.impl.jdbc.SQLExceptionFactory.getSQLException(Unknown Source)
	at org.apache.derby.impl.jdbc.SQLExceptionFactory.getSQLException(Unknown Source)
	at org.apache.derby.impl.jdbc.Util.seeNextException(Unknown Source)
	at org.apache.derby.impl.jdbc.EmbedConnection.createDatabase(Unknown Source)
	at org.apache.derby.impl.jdbc.EmbedConnection.<init>(Unknown Source)
	at org.apa

AnalysisException: org.apache.hadoop.hive.ql.metadata.HiveException: java.lang.RuntimeException: Unable to instantiate org.apache.hadoop.hive.ql.metadata.SessionHiveMetaStoreClient